# Capstone Project - The Battle of Neighborhoods!

Install and import required packages

In [1]:
# install the Google Trends API
# !pip install pytrends

# install the Daft Listings API
!pip install daftlistings

# install the Daft Scraper API
!pip install daft-scraper

# install geopandas, geopy
!pip install geopandas
!pip install geopy

# install folium
!pip install folium

In [2]:
# python packages
import pprint
import requests
import geopandas
import pyproj as pp
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# import k-means from clustering stage
from sklearn.cluster import KMeans

# Google Trends API packages
from pytrends.request import TrendReq

# Daft listings API packages
from daftlistings import Daft, RentType, SortOrder, SortType, MapVisualization, SaleType
from joblib import Parallel, delayed
import time

# Daft Scraper API packages
from daft_scraper.search import DaftSearch, SearchType
from daft_scraper.search.options import (PropertyType, PropertyTypesOption, AdState, AdStateOption)
from daft_scraper.search.options_location import Location, LocationsOption

# convert an address into latitude and longitude values
from geopy.geocoders import Nominatim

import folium # map rendering library

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

In [12]:
dfs = pd.read_html('https://en.wikipedia.org/wiki/List_of_townlands_of_County_Dublin')
df_table = dfs[0]

df_table.head()

Townland Acres           Barony Civil parish Poor law union
0  Abbeyville    80          Coolock     Kinsaley     Balrothery
1  Abbotstown   101      Castleknock  Castleknock   Dublin North
2   Adamstown   111        Newcastle      Aderrig      Celbridge
3   Adamstown   565  Balrothery West   Garristown   Dunshaughlin
4     Aderrig   259        Newcastle      Aderrig      Celbridge

## 1. Introduction
This section outlines a general background for the Business Problem that I'll be trying to solve as part of the capstone project.

The primary focus for this project would be on the city Dublin and its 22 different District areas.  

This project tries to achieve the following analyses for the respective target audience in mind:  
1) **House Renting**: Finding an apartment to rent in Dublin city is very challenging given the housing crisis. The target audience in this case is people looking for rental apartments in the city. The attempt here is to filter out properties based on user preferences for apartment characteristics, neighborhood choices, pricing and crime rate in the neighborhood in which the property is situated.  
2) **Neighborhood Clustering**: The approach here is to use visualization techniques to cluster districts within Dublin city using clustering techniques based on the venues and venue categories present in different districts. We can get a sense of how different districts are oriented within the city in terms of different places, amenities, transport routes and most importantly whether distance from the city centre plays a role in driving this.  
3) **Google Trends**: This data would act as one of the features where we try to do regerssion analysis for predicting the rent price for each apartment. The hypothesis would be that google trends for a search for an apartment to rent in a particular neighborhood would affect the pricing for the rentals. The analysis performed in the subsequent report would test this hypothesis.  
4) **Crimes**: This data would act as additional filtering for users looking to rent an apartment as well as drive the clustering of the districts as planned in point 2 above. It would be intersting to use visualizatin techniques again to find out if crimes are related to the geograhphical attributes of a particular neighborhood.    

Overall the aim is to aid people looking for rentals in Dublin city and help them filter out neighborhoods and properties based on their preferences as well as other local factors driving their decision making.  
Apart from that, the visualiztion techniques used for analysing different datasets would help certain stakeholders make decisions in terms of government planning, business marketing decisions as well as general readers looking for some insights of their own city! 

## 2. Data
This section defines the different data sources as well as their sample examples that have been used for this assignment.

### 2) Daft Listings API
As seen below, this is a very useful API (https://github.com/AnthonyBloomer/daftlistings/) yet simple to use and get upto speed.  
The sample example below shows a search using the API to get all listings in "Dublin city for rental 3-bed apartments with a max price of 2800EUR and furnished".  
We fetch all such listings and build a dataframe containing all the useful features for each property which as seen below would consist of <price', 'facilities', 'formalised_address', 'num_bedrooms', 'num_bathrooms', 'latitude', 'longitude'>  
This data would help us recommend properties to the targeted end-user as well as the geographical  coordinates would help us visually analyse the data in question.  

In [14]:
def translate_listing_to_json(listing):
    try:
        if listing.search_type != 'rental':
            return None
        return listing.as_dict()
    except:
        return None

In [15]:
daft = Daft()
daft.set_county("Dublin City")
daft.set_listing_type(RentType.ANY)
daft.set_max_price(2800)
daft.set_min_beds(3)
daft.set_max_beds(3)
daft.set_furnished(True)
daft.set_sort_order(SortOrder.ASCENDING)
daft.set_sort_by(SortType.PRICE)

In [16]:
listings = daft.search()
properties = []
print("Translating {} listing object into json, it will take a few minutes".format(str(len(listings))))
print("Igonre the error message")

# time the translation
start = time.time()
properties = Parallel(n_jobs=6, prefer="threads")(delayed(translate_listing_to_json)(listing) for listing in listings)
properties = [p for p in properties if p is not None] # remove the None
end = time.time()
print("Time for json translations {}s".format(end-start))

http://www.daft.ie/dublin-city/residential-property-for-rent/?offset=0&s%5Bmnb%5D=3&s%5Bmxb%5D=3&s%5Bfurn%5D=1&s%5Bsort_type%5D=a&s%5Bsort_by%5D=price&s%5Bmxp%5D=2800&s%5Bignored_agents%5D%5B1%5D
Fetched 0 listings.
Translating 0 listing object into json, it will take a few minutes
Igonre the error message
Time for json translations 0.0002739429473876953s


In [17]:
properties

[{'search_type': 'rental',
  'agent_id': '9930',
  'id': '3117037',
  'price': 1500,
  'price_change': None,
  'viewings': [],
  'facilities': ['Parking',
   'Central Heating',
   'Cable Television',
   'Washing Machine',
   'Garden / Patio / Balcony'],
  'overviews': [],
  'formalised_address': '89 Woodbine Park, Raheny, Raheny, Dublin 5, North Dublin City',
  'listing_image': ['https://b.dmlimg.com/NjliYTVjYTk1M2JhZmQyNDkyYTZiMTA5ODFlZjRiN2ZamSgMCE594nq6kbcq7KTGaHR0cDovL3MzLWV1LXdlc3QtMS5hbWF6b25hd3MuY29tL21lZGlhbWFzdGVyLXMzZXUvYi9mL2JmYzZjNjBmNTQwMTY2NDRjNzA3NTcwNDkyZTEwYTk4LmpwZ3x8fDcwMGx8fHx8fHx8.jpg',
   'https://b.dmlimg.com/YTFmMDliMzM3ZTNjNmVjODM1ZDAyNTNjY2RhYzE5NzPgTT-xiHOuDKID4rFsN2TvaHR0cDovL3MzLWV1LXdlc3QtMS5hbWF6b25hd3MuY29tL21lZGlhbWFzdGVyLXMzZXUvNC8yLzQyOWM1ZGQ4NjhiZDI1YTAwZDg2NWYyNDk4YjZkMzllLmpwZ3x8fDcwMGx8fHx8fHx8.jpg',
   'https://b.dmlimg.com/OTc5NTJlMjg5NDYwYzFlMTZiNDhiMjM3NWZmYTkzNjdehCWd4YQUaGpjc-TmXqZ1aHR0cDovL3MzLWV1LXdlc3QtMS5hbWF6b25hd3MuY29tL21lZGlhbWFzdGVy

In [16]:
listings[:5]

[Listing (Dunsoghly, Finglas, Finglas, Dublin 11),
 Listing (Clancy Quay, By Kennedy Wilson, Dublin 8),
 Listing (Castleforbes Square, Castleforbes Road, Ifsc, Dublin 1),
 Listing (Occu Scholarstown Wood, Scholarstown Road, Rathfarnham, Dublin 14),
 Listing (Pipers Court, Hansfield Wood, Hansfield Wood, Clonsilla, Dublin 15)]

In [6]:
df = pd.DataFrame(properties)
df = df[['price', 'facilities', 'formalised_address', 'num_bedrooms', 'num_bathrooms', 'latitude', 'longitude']]
df.head()

price                                         facilities  \
0   1265                                                 []   
1   1592  [Parking, Central Heating, Cable Television, W...   
2   1600  [Parking, Central Heating, House Alarm, Cable ...   
3   1650                                                 []   
4   1695  [Parking, Central Heating, Cable Television, W...   

                                  formalised_address  num_bedrooms  \
0  Grange View Lawn, Clondalkin, Clondalkin, Dubl...             3   
1   Kilcarrig, Tallaght, Dublin 24, South Co. Dublin             3   
2  Decies Road, Ballyfermot, Dublin 10, South Dub...             3   
3           Boroimhe Beech, Swords, North Co. Dublin             3   
4  The Wood, Millbrook Lawns, Tallaght, Dublin 24...             3   

   num_bathrooms            latitude           longitude  
0              1           53.323175           -6.428534  
1              1   53.29276631413049  -6.392316040899743  
2              1           53.340353           -6.339297  
3              2           53.443901           -6.233472  
4              1  53.281367513416114  -6.356052283775597

### 4) Foursquare Places API
Finally, the last part involves a similar approach taken during the previous weeks in this course where we had analysed different neighborhoods in Toronto, Canada.  
The challenge here is to obtain different districts comprising within Dublin City and obtain their respectice geographical coordinates using Nominatim geolocator.  
The sample code given below shows how we plan to construct the final dataframe where each row would be an individual venue along-with the attributes of each of the venues including their geolcation coordinates.  
OneHotEncoding can be used to get a feature representing distribution of different types of venues as well as the most popular and dominating venue type in each of the districts within Dublin city.  

In [92]:
CLIENT_ID = 'WV2XS4MH5YRWGHLTCFT4CKR4SRWNHWAF3JHWHNN4MKEQWTL3' # your Foursquare ID
CLIENT_SECRET = 'QEWWIOG0M3BT4V0YPNSKJY521MDUBHBYWBXCJFZ0452KP3OT' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
limit=100

In [93]:
def getNearbyVenues(names, latitudes, longitudes, radius=5000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            limit)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [83]:
# create map of Dublin using latitude and longitude values
map_dublin = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, neighborhood in zip(dublin_df['Latitude'], dublin_df['Longitude'], dublin_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_dublin)  
    
map_dublin

In [85]:
print('There are {} uniques categories.'.format(len(dublin_venues['Venue Category'].unique())))

There are 192 uniques categories.


In [86]:
# one hot encoding
dublin_onehot = pd.get_dummies(dublin_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
dublin_onehot['Neighborhood'] = dublin_venues['Neighborhood'] 

# move neighborhood column to the first column
cols = list(dublin_onehot)
cols.insert(0, cols.pop(cols.index('Neighborhood')))
dublin_onehot = dublin_onehot.loc[:, cols]

dublin_onehot.head()

Neighborhood  American Restaurant  Arcade  Art Gallery  Art Museum  \
0     Dublin 1                    0       0            0           0   
1     Dublin 1                    0       0            0           0   
2     Dublin 1                    0       0            0           0   
3     Dublin 1                    0       0            0           0   
4     Dublin 1                    0       0            0           0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  BBQ Joint  \
0                 0                   0                      0          0   
1                 0                   0                      0          0   
2                 0                   0                      0          0   
3                 0                   0                      0          0   
4                 0                   0                      0          0   

   Bagel Shop  Bakery  Bar  Basketball Stadium  Beach  Bed & Breakfast  \
0           0       0    0                   0      0                0   
1           0       0    0                   0      0                0   
2           0       0    0                   0      0                0   
3           0       0    0                   0      0                0   
4           0       0    0                   0      0                0   

   Beer Bar  Betting Shop  Bike Rental / Bike Share  Bistro  Boat or Ferry  \
0         0             0                         0       0              0   
1         0             0                         0       0              0   
2         0             0                         0       0              0   
3         0             0                         0       0              0   
4         0             0                         0       0              0   

   Bookstore  Botanical Garden  Bowling Alley  Breakfast Spot  Brewery  \
0          0                 0              0               0        0   
1          0                 0              0               0        0   
2          0                 0              0               0        0   
3          0                 0              0               0        0   
4          0                 0              0               0        0   

   Bridge  Buffet  Burger Joint  Burrito Place  Bus Stop  Café  Canal  \
0       0       0             0              0         0     0      0   
1       0       0             0              0         0     0      0   
2       0       0             0              0         0     0      0   
3       0       0             0              0         0     0      0   
4       0       0             0              0         0     0      0   

   Canal Lock  Castle  Cheese Shop  Chinese Restaurant  Chocolate Shop  \
0           0       0            0                   0               0   
1           0       0            0                   0               0   
2           0       0            0                   0               0   
3           0       0            0                   0               0   
4           0       0            0                   0               0   

   Climbing Gym  Clothing Store  Cocktail Bar  Coffee Shop  Comic Shop  \
0             0               0             0            0           0   
1             0               0             0            0           0   
2             0               0             0            0           0   
3             0               0             0            0           0   
4             0               1             0            0           0   

   Concert Hall  Convenience Store  Convention Center  Creperie  \
0             0                  0                  0         0   
1             0                  0                  0         0   
2             0                  0                  0         0   
3             0                  0                  0         0   
4             0                  0                  0         0   

   Deli / Bodeg

In [87]:
dublin_onehot.shape

(1646, 193)

In [89]:
dublin_grouped = dublin_onehot.groupby('Neighborhood').mean().reset_index()
dublin_grouped

Neighborhood  American Restaurant  Arcade  Art Gallery  Art Museum  \
0      Ballinteer             0.000000    0.00     0.000000    0.000000   
1       Blackrock             0.000000    0.00     0.000000    0.000000   
2      Clondalkin             0.000000    0.00     0.000000    0.000000   
3        Dublin 1             0.000000    0.00     0.000000    0.000000   
4       Dublin 10             0.000000    0.00     0.000000    0.000000   
5       Dublin 11             0.000000    0.00     0.000000    0.000000   
6       Dublin 12             0.000000    0.00     0.000000    0.000000   
7       Dublin 13             0.000000    0.00     0.000000    0.000000   
8       Dublin 14             0.010000    0.00     0.000000    0.000000   
9       Dublin 15             0.012987    0.00     0.000000    0.000000   
10      Dublin 17             0.000000    0.00     0.000000    0.000000   
11      Dublin 18             0.000000    0.00     0.000000    0.000000   
12       Dublin 2             0.000000    0.00     0.000000    0.000000   
13      Dublin 20             0.016667    0.00     0.000000    0.000000   
14       Dublin 3             0.000000    0.00     0.000000    0.000000   
15       Dublin 4             0.000000    0.00     0.000000    0.000000   
16       Dublin 5             0.000000    0.00     0.000000    0.000000   
17       Dublin 6             0.000000    0.00     0.000000    0.000000   
18      Dublin 6W             0.000000    0.00     0.000000    0.000000   
19       Dublin 7             0.000000    0.01     0.000000    0.000000   
20       Dublin 8             0.000000    0.00     0.013889    0.013889   
21       Dublin 9             0.000000    0.00     0.000000    0.000000   
22  Dun Laoghaire             0.000000    0.00     0.000000    0.000000   
23         Swords             0.013889    0.00     0.000000    0.000000   
24       Tallaght             0.000000    0.00     0.018519    0.000000   

    Asian Restaurant  Athletics & Sports  Australian Restaurant  BBQ Joint  \
0           0.013158            0.000000               0.000000       0.00   
1           0.000000            0.000000               0.000000       0.00   
2           0.000000            0.027778               0.000000       0.00   
3           0.000000            0.000000               0.000000       0.00   
4           0.000000            0.000000               0.000000       0.00   
5           0.000000            0.000000               0.000000       0.00   
6           0.000000            0.025641               0.000000       0.00   
7           0.000000            0.000000               0.000000       0.00   
8           0.020000            0.000000               0.000000       0.00   
9           0.038961            0.000000               0.000000       0.00   
10          0.000000            0.022727               0.000000       0.00   
11          0.000000            0.032258               0.000000       0.00   
12          0.000000            0.000000               0.000000       0.00   
13          0.016667            0.000000               0.000000       0.00   
14          0.000000            0.000000               0.000000       0.00   
15          0.010000            0.000000               0.000000       0.00   
16          0.000000            0.000000               0.000000       0.00   
17          0.000000            0.000000               0.000000       0.00   
18          0.013699            0.000000               0.000000       0.00   
19          0.000000            0.000000               0.000000       0.01   
20          0.000000            0.000000               0.000000       0.00   
21          0.016949            0.000000               0.000000       0.00   
22          0.000000            0.000000               0.000000       0.00   
23          0.000000            0.000000               0.000000       0.00   
24          0.018519            0.018519               0.018519       0.00   

    Bagel Shop    Bakery 

In [90]:
dublin_grouped.shape

(25, 193)

In [91]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [95]:
num_top_venues = 10
indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = dublin_grouped['Neighborhood']

for ind in np.arange(dublin_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(dublin_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood 1st Most Common Venue   2nd Most Common Venue  \
0      Ballinteer           Supermarket                    Café   
1       Blackrock                   Pub                    Café   
2      Clondalkin                 Hotel                     Bar   
3        Dublin 1           Coffee Shop                    Café   
4       Dublin 10           Supermarket                     Pub   
5       Dublin 11           Supermarket                    Park   
6       Dublin 12           Supermarket                    Park   
7       Dublin 13    Seafood Restaurant                     Pub   
8       Dublin 14           Supermarket                     Pub   
9       Dublin 15           Coffee Shop             Supermarket   
10      Dublin 17           Supermarket    Fast Food Restaurant   
11      Dublin 18   Sporting Goods Shop  Furniture / Home Store   
12       Dublin 2                  Café             Coffee Shop   
13      Dublin 20  Fast Food Restaurant                   Hotel   
14       Dublin 3                  Café                     Pub   
15       Dublin 4                   Pub                    Café   
16       Dublin 5           Supermarket           Grocery Store   
17       Dublin 6            Restaurant                     Pub   
18      Dublin 6W                   Pub             Supermarket   
19       Dublin 7                   Pub                    Café   
20       Dublin 8                   Pub             Zoo Exhibit   
21       Dublin 9           Supermarket                     Pub   
22  Dun Laoghaire           Coffee Shop                     Pub   
23         Swords           Coffee Shop             Supermarket   
24       Tallaght           Supermarket                     Pub   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                    Pub           Coffee Shop        Clothing Store   
1          Train Station                  Park           Coffee Shop   
2      Convenience Store           Coffee Shop            Restaurant   
3                    Pub                  Park    Italian Restaurant   
4                   Park                   Gym                 Hotel   
5      Convenience Store                   Pub         Grocery Store   
6      Convenience Store  Fast Food Restaurant          Tram Station   
7                   Café           Fish Market        Ice Cream Shop   
8            Coffee Shop        Clothing Store                  Café   
9         Clothing Store    Italian Restaurant         Train Station   
10           Coffee Shop              Bus Stop         Shopping Mall   
11    Light Rail Station                  Café           Coffee Shop   
12                  Park                 Hotel                 Plaza   
13                  Park           Coffee Shop        Clothing Store   
14         Boat or Ferry                 Beach                  Park   
15            Restaurant           Coffee Shop                 Hotel   
16         Train Station     Convenience Store  Fast Food Restaurant   
17                  Café                  Park           Coffee Shop   
18     Convenience Store                  Park            Restaurant   
19           Coffee Shop                  Park            Restaurant   
20                  Park         Historic Site           Coffee Shop   
21                  Park         Grocery Store                  Café   
22                  Café                  Park    Italian Restaurant   
23                   Pub                   Bar         Grocery Store   
24  Fast Food Restaurant    Light Rail Station     Electronics Store   

   6th Most Common Venue   7th Most Common Venue   8th Most Common Venue  \
0       Department Store                     Gym  Furniture / Home Store   
1          Shopping Mall             Supermarket                     Bar   
2            Supermarket      Chinese Restaurant      Light Rail Station   
3                  Hotel               Bookstore                 Theater   
4        

In [101]:
# set number of clusters
kclusters = 3

dublin_grouped_clustering = dublin_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(dublin_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([1, 1, 1, 0, 2, 2, 2, 0, 1, 1, 2, 1, 0, 1, 1, 0, 2, 0, 2, 0, 1, 2,
       0, 1, 2], dtype=int32)

In [100]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

dublin_merged = dublin_df

# merge dublin_grouped with dublin_merged to add latitude/longitude for each neighborhood
dublin_merged = dublin_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
dublin_merged['Cluster Labels'].fillna(3.0, inplace=True)
dublin_merged['Cluster Labels'] = dublin_merged['Cluster Labels'].astype(int)

dublin_merged.head() # check the last columns!

Neighborhood   Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
0     Dublin 1  53.352488  -6.256646               0           Coffee Shop   
1     Dublin 2  53.338940  -6.252713               0                  Café   
2     Dublin 3  53.361223  -6.185467               1                  Café   
3     Dublin 4  53.327507  -6.227486               0                   Pub   
4     Dublin 5  53.383454  -6.181923               2           Supermarket   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Café                   Pub                  Park   
1           Coffee Shop                  Park                 Hotel   
2                   Pub         Boat or Ferry                 Beach   
3                  Café            Restaurant           Coffee Shop   
4         Grocery Store         Train Station     Convenience Store   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0    Italian Restaurant                 Hotel             Bookstore   
1                 Plaza                   Pub            Restaurant   
2                  Park        Scenic Lookout     Convenience Store   
3                 Hotel                  Park         Grocery Store   
4  Fast Food Restaurant                   Pub         Shopping Mall   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0               Theater                   Bar                  Plaza  
1          Cocktail Bar         Grocery Store                 Bakery  
2         Train Station            Restaurant                   Port  
3             Gastropub           Pizza Place                  Plaza  
4                  Café           Pizza Place               Bus Stop

In [131]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10.2)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(dublin_merged['Latitude'], dublin_merged['Longitude'], dublin_merged['Neighborhood'], dublin_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=6,
        popup=label,
        color=rainbow[cluster],
        fill=True,
        fill_color=rainbow[cluster],
        fill_opacity=0.3).add_to(map_clusters)
       
map_clusters

In [3]:
options = [
    PropertyTypesOption([PropertyType.ALL]),
    LocationsOption([Location.DUBLIN_COUNTY]),
    AdStateOption(AdState.AGREED)
]

api = DaftSearch(SearchType.SALE)
listings = api.search(options)

In [4]:
print(len(listings))

cnt_price = 0
cnt_abr_price = 0

for listing in listings:
    if hasattr(listing, 'price'):
        cnt_price += 1
    if hasattr(listing, 'abbreviatedPrice'):
        cnt_abr_price += 1

print(cnt_price, cnt_abr_price)

3420
3315 3420


In [5]:
test_df2 = pd.DataFrame([vars(f) for f in listings])

In [6]:
test_df2.head()

title    saleType  numBedrooms  \
0    Lynton, Old Connaught Avenue, Bray, Co. Wicklow  [For Sale]          5.0   
1             171 Drimnagh Road, Drimnagh, Dublin 12  [For Sale]          2.0   
2              19 Annaville Park, Dundrum, Dublin 14  [For Sale]          3.0   
3          18a Millgate Drive, Perrystown, Dublin 12  [For Sale]          3.0   
4  Robswall by Hollybrook Homes, Coast Road, Mala...  [For Sale]          2.0   

         state                                    seoFriendlyPath  \
0  SALE_AGREED  /new-home-for-sale/lynton-old-connaught-avenue...   
1  SALE_AGREED  /for-sale/apartment-171-drimnagh-road-drimnagh...   
2  SALE_AGREED  /for-sale/semi-detached-house-19-annaville-par...   
3  SALE_AGREED  /for-sale/detached-house-18a-millgate-drive-pe...   
4  SALE_AGREED  /new-home-for-sale/robswall-by-hollybrook-home...   

  daftShortcode      _id abbreviatedPrice   category  \
0       9190876  2554301            €745k  New Homes   
1      13526488  2871652            €225k        Buy   
2      13445297  2859219            €695k        Buy   
3      13355550  2844684            €600k        Buy   
4        941204  1118178            €680k  New Homes   

                                              seller  \
0  {'name': 'Derek Byrne', 'sellerType': 'BRANDED...   
1  {'name': 'Gerry', 'sellerType': 'UNBRANDED_AGE...   
2  {'profileImage': 'https://photos.cdn.dsch.ie/M...   
3  {'name': 'Sineád Beggan', 'sellerType': 'BRAND...   
4  {'alternativePhone': '01 634 2466', 'profileIm...   

                                                 ber  \
0                                   {'rating': 'A3'}   
1                                    {'rating': 'G'}   
2  {'code': '104258587', 'rating': 'B3', 'epi': '...   
3                                                NaN   
4                                   {'rating': 'A3'}   

                                            sections propertyType  \
0                      [Property, New Homes, Houses]       Houses   
1                 [Property, Residential, Apartment]    Apartment   
2  [Property, Residential, House, Semi-Detached H...       Semi-D   
3     [Property, Residential, House, Detached House]     Detached   
4                      [Property, New Homes, Houses]       Houses   

                                            seoTitle  \
0    Lynton, Old Connaught Avenue, Bray, Co. Wicklow   
1             171 Drimnagh Road, Drimnagh, Dublin 12   
2              19 Annaville Park, Dundrum, Dublin 14   
3          18a Millgate Drive, Perrystown, Dublin 12   
4  Robswall by Hollybrook Homes, Coast Road, Mala...   

                                               point    publishDate  \
0  {'point_type': 'Point', 'coordinates': [-6.119...  1601485470000   
1  {'point_type': 'Point', 'coordinates': [-6.326...  1612010827000   
2  {'point_type': 'Point', 'coordinates': [-6.244...  1611307556000   
3  {'point_type': 'Point', 'coordinates': [-6.320...  1612229525000   
4  {'point_type': 'Point', 'coordinates': [-6.134...  1605640420000   

  featuredLevel                                              media  \
0      FEATURED  {'hasBrochure': False, 'totalImages': 5, 'imag...   
1      FEATURED  {'hasBrochure': False, 'totalImages': 7, 'imag...   
2      FEATURED  {'hasBrochure': False, 'totalImages': 15, 'ima...   
3      FEATURED  {'hasBrochure': False, 'totalImages': 18, 'ima...   
4      FEATURED  {'hasBrochure': True, 'totalImages': 11, 'imag...   

         label                                       pageBranding  \
0  SALE AGREED  {'standardLogo': 'https://photos.cdn.dsch.ie/Z...   
1  SALE AGREED  {'backgroundColour': '#f4f4f4', 'squareLogos':...   
2  SALE AGREED  {'standardLogo': 'https://photos.cdn.dsch.ie/N...   
3  SALE AGREED  {'standardLogo': 'https://photos.cdn.dsch.ie/N...   
4  SALE AGREED  {'standardLogo': 'https://photos.cdn.dsch.ie/M...   

                                             newHome  \
0  {'totalUnitTypes': 1, 'subUnits': [{'id': 2554...   
1      

In [30]:
final_df = test_df2[['title', 'propertyType', 'category', 'numBedrooms', 'numBathrooms', 'price', 'abbreviatedPrice', 'ber', 'point', 'publishDate']]

In [31]:
final_df.head()

title propertyType   category  \
0    Lynton, Old Connaught Avenue, Bray, Co. Wicklow       Houses  New Homes   
1             171 Drimnagh Road, Drimnagh, Dublin 12    Apartment        Buy   
2              19 Annaville Park, Dundrum, Dublin 14       Semi-D        Buy   
3          18a Millgate Drive, Perrystown, Dublin 12     Detached        Buy   
4  Robswall by Hollybrook Homes, Coast Road, Mala...       Houses  New Homes   

   numBedrooms  numBathrooms     price abbreviatedPrice  \
0          5.0           NaN       NaN            €745k   
1          2.0           1.0  225000.0            €225k   
2          3.0           2.0  695000.0            €695k   
3          3.0           1.0  600000.0            €600k   
4          2.0           NaN       NaN            €680k   

                                                 ber  \
0                                   {'rating': 'A3'}   
1                                    {'rating': 'G'}   
2  {'code': '104258587', 'rating': 'B3', 'epi': '...   
3                                                NaN   
4                                   {'rating': 'A3'}   

                                               point    publishDate  
0  {'point_type': 'Point', 'coordinates': [-6.119...  1601485470000  
1  {'point_type': 'Point', 'coordinates': [-6.326...  1612010827000  
2  {'point_type': 'Point', 'coordinates': [-6.244...  1611307556000  
3  {'point_type': 'Point', 'coordinates': [-6.320...  1612229525000  
4  {'point_type': 'Point', 'coordinates': [-6.134...  1605640420000

In [32]:
new = final_df["title"].str.split(",", n = 6, expand = True) 

new[5].fillna(new[4], inplace=True)
new[5].fillna(new[3], inplace=True)
new[5].fillna(new[2], inplace=True)
new[5].fillna(new[1], inplace=True)
new[5].fillna(new[0], inplace=True)

In [33]:
final_df["neighbourhood"]= new[5] 

/Users/yashkarle/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [34]:
col = 'neighbourhood'
n = 10
final_df = final_df[final_df.groupby(col)[col].transform('count').ge(n)]

vague_n = final_df[final_df['neighbourhood'] == ' Co. Dublin'].index
final_df.drop(vague_n , inplace=True)

In [35]:
final_df.groupby(['neighbourhood']).size()

neighbourhood
 Dublin 1      74
 Dublin 10     34
 Dublin 11    175
 Dublin 12    166
 Dublin 13    127
 Dublin 14    162
 Dublin 15    275
 Dublin 16     87
 Dublin 17     12
 Dublin 18    140
 Dublin 2      37
 Dublin 20     20
 Dublin 22     88
 Dublin 24    132
 Dublin 3     146
 Dublin 4     125
 Dublin 5     141
 Dublin 6     141
 Dublin 6W     39
 Dublin 7     126
 Dublin 8     175
 Dublin 9     168
dtype: int64

In [36]:
len(final_df)

2590

In [37]:
final_df['val'] = final_df['abbreviatedPrice'].str.replace('€','')
final_df['val'] = final_df['val'].str.replace('+','')
final_df['val'] = final_df['val'].str.replace('POA','0')

final_df.val = (final_df.val.replace(r'[kM]+$', '', regex=True).astype(float) * final_df.val.str.extract(r'[\d\.]+([kM]+)', expand=False).fillna(1).replace(['k','M'], [10**3, 10**6]).astype(int))

final_df.price.fillna(final_df.val, inplace=True)

In [38]:
final_df.head()

title propertyType category  \
1             171 Drimnagh Road, Drimnagh, Dublin 12    Apartment      Buy   
2              19 Annaville Park, Dundrum, Dublin 14       Semi-D      Buy   
3          18a Millgate Drive, Perrystown, Dublin 12     Detached      Buy   
5  Site with F.P.P for Superior Detached Home, 22...         Site      Buy   
6  Apartment 78, The Hibernian, The Gasworks, Gra...    Apartment      Buy   

   numBedrooms  numBathrooms     price abbreviatedPrice  \
1          2.0           1.0  225000.0            €225k   
2          3.0           2.0  695000.0            €695k   
3          3.0           1.0  600000.0            €600k   
5          NaN           NaN  498000.0            €498k   
6          1.0           1.0  375000.0            €375k   

                                                 ber  \
1                                    {'rating': 'G'}   
2  {'code': '104258587', 'rating': 'B3', 'epi': '...   
3                                                NaN   
5                                                NaN   
6  {'code': '113469167', 'rating': 'B3', 'epi': '...   

                                               point    publishDate  \
1  {'point_type': 'Point', 'coordinates': [-6.326...  1612010827000   
2  {'point_type': 'Point', 'coordinates': [-6.244...  1611307556000   
3  {'point_type': 'Point', 'coordinates': [-6.320...  1612229525000   
5  {'point_type': 'Point', 'coordinates': [-6.292...  1611837188000   
6  {'point_type': 'Point', 'coordinates': [-6.235...  1611134300000   

  neighbourhood       val  
1     Dublin 12  225000.0  
2     Dublin 14  695000.0  
3     Dublin 12  600000.0  
5      Dublin 6  498000.0  
6      Dublin 4  375000.0

In [41]:
test_df3 = pd.concat([final_df.drop(['point'], axis=1), final_df['point'].apply(pd.Series)], axis=1)

test_df3[['longitude','latitude']] = pd.DataFrame(test_df3.coordinates.tolist(), index=test_df3.index)

In [42]:
test_df3.head()

title propertyType category  \
1             171 Drimnagh Road, Drimnagh, Dublin 12    Apartment      Buy   
2              19 Annaville Park, Dundrum, Dublin 14       Semi-D      Buy   
3          18a Millgate Drive, Perrystown, Dublin 12     Detached      Buy   
5  Site with F.P.P for Superior Detached Home, 22...         Site      Buy   
6  Apartment 78, The Hibernian, The Gasworks, Gra...    Apartment      Buy   

   numBedrooms  numBathrooms     price abbreviatedPrice  \
1          2.0           1.0  225000.0            €225k   
2          3.0           2.0  695000.0            €695k   
3          3.0           1.0  600000.0            €600k   
5          NaN           NaN  498000.0            €498k   
6          1.0           1.0  375000.0            €375k   

                                                 ber    publishDate  \
1                                    {'rating': 'G'}  1612010827000   
2  {'code': '104258587', 'rating': 'B3', 'epi': '...  1611307556000   
3                                                NaN  1612229525000   
5                                                NaN  1611837188000   
6  {'code': '113469167', 'rating': 'B3', 'epi': '...  1611134300000   

  neighbourhood       val point_type  \
1     Dublin 12  225000.0      Point   
2     Dublin 14  695000.0      Point   
3     Dublin 12  600000.0      Point   
5      Dublin 6  498000.0      Point   
6      Dublin 4  375000.0      Point   

                                coordinates  longitude   latitude  
1                    [-6.326964, 53.323975]  -6.326964  53.323975  
2                    [-6.244434, 53.298543]  -6.244434  53.298543  
3                    [-6.32089, 53.3077253]  -6.320890  53.307725  
5  [-6.2926110389430505, 53.30761348842631]  -6.292611  53.307613  
6                    [-6.235775, 53.338922]  -6.235775  53.338922

In [43]:
test_df3 = pd.concat([test_df3.drop(['ber'], axis=1), test_df3['ber'].apply(pd.Series)], axis=1)

In [44]:
test_df3.head()

title propertyType category  \
1             171 Drimnagh Road, Drimnagh, Dublin 12    Apartment      Buy   
2              19 Annaville Park, Dundrum, Dublin 14       Semi-D      Buy   
3          18a Millgate Drive, Perrystown, Dublin 12     Detached      Buy   
5  Site with F.P.P for Superior Detached Home, 22...         Site      Buy   
6  Apartment 78, The Hibernian, The Gasworks, Gra...    Apartment      Buy   

   numBedrooms  numBathrooms     price abbreviatedPrice    publishDate  \
1          2.0           1.0  225000.0            €225k  1612010827000   
2          3.0           2.0  695000.0            €695k  1611307556000   
3          3.0           1.0  600000.0            €600k  1612229525000   
5          NaN           NaN  498000.0            €498k  1611837188000   
6          1.0           1.0  375000.0            €375k  1611134300000   

  neighbourhood       val point_type  \
1     Dublin 12  225000.0      Point   
2     Dublin 14  695000.0      Point   
3     Dublin 12  600000.0      Point   
5      Dublin 6  498000.0      Point   
6      Dublin 4  375000.0      Point   

                                coordinates  longitude   latitude   0  \
1                    [-6.326964, 53.323975]  -6.326964  53.323975 NaN   
2                    [-6.244434, 53.298543]  -6.244434  53.298543 NaN   
3                    [-6.32089, 53.3077253]  -6.320890  53.307725 NaN   
5  [-6.2926110389430505, 53.30761348842631]  -6.292611  53.307613 NaN   
6                    [-6.235775, 53.338922]  -6.235775  53.338922 NaN   

        code               epi rating  
1        NaN               NaN      G  
2  104258587  129.85 kWh/m2/yr     B3  
3        NaN               NaN    NaN  
5        NaN               NaN    NaN  
6  113469167  130.12 kWh/m2/yr     B3

In [54]:
final_df2 = test_df3[['title', 'neighbourhood', 'propertyType', 'numBedrooms', 'numBathrooms', 'val', 'rating', 'longitude', 'latitude']]

In [55]:
final_df2.head()

title neighbourhood  \
1             171 Drimnagh Road, Drimnagh, Dublin 12     Dublin 12   
2              19 Annaville Park, Dundrum, Dublin 14     Dublin 14   
3          18a Millgate Drive, Perrystown, Dublin 12     Dublin 12   
5  Site with F.P.P for Superior Detached Home, 22...      Dublin 6   
6  Apartment 78, The Hibernian, The Gasworks, Gra...      Dublin 4   

  propertyType  numBedrooms  numBathrooms       val rating  longitude  \
1    Apartment          2.0           1.0  225000.0      G  -6.326964   
2       Semi-D          3.0           2.0  695000.0     B3  -6.244434   
3     Detached          3.0           1.0  600000.0    NaN  -6.320890   
5         Site          NaN           NaN  498000.0    NaN  -6.292611   
6    Apartment          1.0           1.0  375000.0     B3  -6.235775   

    latitude  
1  53.323975  
2  53.298543  
3  53.307725  
5  53.307613  
6  53.338922

In [81]:
final_df2[final_df2['numBathrooms'].isnull()].groupby(['propertyType']).size()

propertyType
Apartment         13
Bungalow           2
Detached           6
End of Terrace     1
Houses             3
Semi-D             5
Site              17
Studio             1
Terrace           15
dtype: int64

In [88]:
final_df2.groupby(['rating']).size()

rating
A2         17
A3         34
B1          7
B2         83
B3        182
C1        213
C2        247
C3        234
D1        293
D2        311
E1        234
E2        185
F         175
G         142
SI_666     60
dtype: int64

In [90]:
final_df2['numBedrooms'] = final_df2['numBedrooms'].fillna(-1)

final_df2['numBathrooms'] = final_df2['numBathrooms'].fillna(-1)

final_df2['rating'] = final_df2['rating'].fillna('ZZZ')

In [91]:
final_df2.head()

title neighbourhood  \
1             171 Drimnagh Road, Drimnagh, Dublin 12     Dublin 12   
2              19 Annaville Park, Dundrum, Dublin 14     Dublin 14   
3          18a Millgate Drive, Perrystown, Dublin 12     Dublin 12   
5  Site with F.P.P for Superior Detached Home, 22...      Dublin 6   
6  Apartment 78, The Hibernian, The Gasworks, Gra...      Dublin 4   

  propertyType  numBedrooms  numBathrooms       val rating  longitude  \
1    Apartment          2.0           1.0  225000.0      G  -6.326964   
2       Semi-D          3.0           2.0  695000.0     B3  -6.244434   
3     Detached          3.0           1.0  600000.0    ZZZ  -6.320890   
5         Site         -1.0          -1.0  498000.0    ZZZ  -6.292611   
6    Apartment          1.0           1.0  375000.0     B3  -6.235775   

    latitude  
1  53.323975  
2  53.298543  
3  53.307725  
5  53.307613  
6  53.338922

In [103]:
mapping_df = final_df2[:1000]

In [95]:
address = 'Dublin, Ireland'

geolocator = Nominatim(user_agent="dublin_locator")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Dublin are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Dublin are 53.3497645, -6.2602732.


In [125]:
# create map of Dublin using latitude and longitude values
map_dublin = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, title, neigh in zip(mapping_df['latitude'], mapping_df['longitude'], mapping_df['title'], mapping_df['neighbourhood']):
    label = '{}'.format(title)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        popup=label,
        color=neigh,
        fill=True,
        fill_color=neigh,
        fill_opacity=0.7,
        parse_html=False).add_to(map_dublin)  
    
map_dublin

In [105]:
final_df2.head()

title neighbourhood  \
1             171 Drimnagh Road, Drimnagh, Dublin 12     Dublin 12   
2              19 Annaville Park, Dundrum, Dublin 14     Dublin 14   
3          18a Millgate Drive, Perrystown, Dublin 12     Dublin 12   
5  Site with F.P.P for Superior Detached Home, 22...      Dublin 6   
6  Apartment 78, The Hibernian, The Gasworks, Gra...      Dublin 4   

  propertyType  numBedrooms  numBathrooms       val rating  longitude  \
1    Apartment          2.0           1.0  225000.0      G  -6.326964   
2       Semi-D          3.0           2.0  695000.0     B3  -6.244434   
3     Detached          3.0           1.0  600000.0    ZZZ  -6.320890   
5         Site         -1.0          -1.0  498000.0    ZZZ  -6.292611   
6    Apartment          1.0           1.0  375000.0     B3  -6.235775   

    latitude  
1  53.323975  
2  53.298543  
3  53.307725  
5  53.307613  
6  53.338922